# ప్రొడక్షన్‌లో AutoGen ఏజెంట్లు: గమనిక & మూల్యాంకనం

ఈ ట్యుటోరియల్‌లో, **[Autogen ఏజెంట్లు](https://github.com/microsoft/autogen)** యొక్క అంతర్గత దశలను (ట్రేస్‌లు) **మానిటర్ చేయడం** మరియు **దాని పనితీరును మూల్యాంకనం చేయడం** ఎలా చేయాలో [Langfuse](https://langfuse.com) ఉపయోగించి నేర్చుకుంటాము.

ఈ గైడ్ **ఆన్‌లైన్** మరియు **ఆఫ్‌లైన్** మూల్యాంకన ప్రమాణాలను కవర్ చేస్తుంది, ఇవి ఏజెంట్లను వేగంగా మరియు నమ్మకంగా ప్రొడక్షన్‌కు తీసుకురావడానికి టీమ్‌లు ఉపయోగిస్తాయి.

**AI ఏజెంట్ మూల్యాంకనం ఎందుకు ముఖ్యమైంది:**
- పనులు విఫలమయ్యే లేదా తక్కువ స్థాయి ఫలితాలను ఉత్పత్తి చేసే సందర్భాల్లో సమస్యలను డీబగ్ చేయడం
- ఖర్చులు మరియు పనితీరును రియల్-టైమ్‌లో గమనించడం
- నిరంతర ఫీడ్‌బ్యాక్ ద్వారా నమ్మకాన్ని మరియు భద్రతను మెరుగుపరచడం


## దశ 1: పర్యావరణ వేరియబుల్స్ సెట్ చేయండి

మీ Langfuse API కీలు పొందడానికి [Langfuse Cloud](https://cloud.langfuse.com/) కోసం సైన్ అప్ చేయండి లేదా [Langfuse స్వీయ-హోస్టింగ్](https://langfuse.com/self-hosting) ఉపయోగించండి.

_**గమనిక:** స్వీయ-హోస్టర్లు [Terraform మాడ్యూల్స్](https://langfuse.com/self-hosting/azure) ఉపయోగించి Azure లో Langfuse ను డిప్లాయ్ చేయవచ్చు. ప్రత్యామ్నాయంగా, మీరు [Helm చార్ట్](https://langfuse.com/self-hosting/kubernetes-helm) ఉపయోగించి Kubernetes లో Langfuse ను డిప్లాయ్ చేయవచ్చు._


In [5]:
import os

# Get keys for your project from the project settings page: https://cloud.langfuse.com
os.environ["LANGFUSE_PUBLIC_KEY"] = "pk-lf-..." 
os.environ["LANGFUSE_SECRET_KEY"] = "sk-lf-..." 
os.environ["LANGFUSE_HOST"] = "https://cloud.langfuse.com" # 🇪🇺 EU region
# os.environ["LANGFUSE_HOST"] = "https://us.cloud.langfuse.com" # 🇺🇸 US region

In [1]:
!pip install langfuse openlit


[notice] A new release of pip is available: 25.1.1 -> 25.2
[notice] To update, run: pip install --upgrade pip


పర్యావరణ వేరియబుల్స్ సెట్ చేసిన తర్వాత, ఇప్పుడు Langfuse క్లయింట్‌ను ప్రారంభించవచ్చు. `get_client()` పద్ధతి పర్యావరణ వేరియబుల్స్‌లో అందించిన క్రెడెన్షియల్స్‌ను ఉపయోగించి Langfuse క్లయింట్‌ను ప్రారంభిస్తుంది.


In [6]:
from langfuse import Langfuse
 
# Filter out Autogen OpenTelemetryspans
langfuse = Langfuse(
    blocked_instrumentation_scopes=["autogen SingleThreadedAgentRuntime"]
)
 
# Verify connection
if langfuse.auth_check():
    print("Langfuse client is authenticated and ready!")
else:
    print("Authentication failed. Please check your credentials and host.")

Langfuse client is authenticated and ready!


## దశ 2: OpenLit ఇన్‌స్ట్రుమెంటేషన్ ప్రారంభించండి

ఇప్పుడు, మేము [OpenLit](https://github.com/openlit/openlit) ఇన్‌స్ట్రుమెంటేషన్‌ను ప్రారంభిస్తాము. OpenLit స్వయంచాలకంగా AutoGen ఆపరేషన్లను క్యాప్చర్ చేసి OpenTelemetry (OTel) స్పాన్లను Langfuseకి ఎగుమతి చేస్తుంది.


In [7]:
import openlit
 
# Initialize OpenLIT instrumentation. The disable_batch flag is set to true to process traces immediately.
openlit.init(tracer=langfuse._otel_tracer, disable_batch=True, disabled_instrumentors=["mistral"])

## దశ 3: మీ ఏజెంట్‌ను నడపండి

ఇప్పుడు మనం మా ఇన్‌స్ట్రుమెంటేషన్‌ను పరీక్షించడానికి మల్టీ టర్న్ ఏజెంట్‌ను సెట్ చేస్తాము.


In [2]:
import os

from autogen_agentchat.agents import AssistantAgent
from autogen_ext.models.azure import AzureAIChatCompletionClient
from azure.core.credentials import AzureKeyCredential
from autogen_agentchat.base import TaskResult

from autogen_agentchat.conditions import TextMentionTermination
from autogen_agentchat.teams import RoundRobinGroupChat

In [3]:
client = AzureAIChatCompletionClient(
    model="gpt-4o-mini",
    endpoint="https://models.inference.ai.azure.com",
    # To authenticate with the model you will need to generate a personal access token (PAT) in your GitHub settings.
    # Create your PAT token by following instructions here: https://docs.github.com/en/authentication/keeping-your-account-and-data-secure/managing-your-personal-access-tokens
    credential=AzureKeyCredential(os.environ["GITHUB_TOKEN"]),
    model_info={
        "json_output": True,
        "function_calling": True,
        "vision": True,
        "family": "unknown",
        "structured_output": False
    },
)

In [8]:
# 🍴 Agent 1 – proposes ONE healthy meal idea each turn
meal_planner_agent = AssistantAgent(
    "meal_planner_agent",
    model_client=client,
    description="A seasoned meal-planning coach who suggests balanced meals.",
    system_message="""
    You are a Meal-Planning Assistant with a decade of experience helping busy people prepare meals.
    Goal: propose the single best meal (breakfast, lunch, or dinner) given the user's context.
    Each response must contain ONLY one complete meal idea (title + very brief component list) — no extras.
    Keep it concise: skip greetings, chit-chat, and filler.
    """,
)

# 🥗 Agent 2 – checks nutritional quality & variety
nutritionist_agent = AssistantAgent(
    "nutritionist_agent",
    model_client=client,
    description="A registered dietitian ensuring meals meet nutritional standards.",
    system_message="""
    You are a Nutritionist focused on whole-food, macro-balanced eating.
    Evaluate the meal_planner_agent’s recommendation.
    If the meal is nutritionally sound, sufficiently varied, and portion-appropriate, respond with 'APPROVE'.
    Otherwise, give high-level guidance on how to improve it (e.g. 'add a plant-based protein') — do NOT provide a full alternative recipe.
    """,
)

In [9]:
# ✅ Chat stops once the nutritionist says APPROVE
termination = TextMentionTermination("APPROVE")

# 🔄 Alternate turns between the two agents until termination
team = RoundRobinGroupChat(
    [meal_planner_agent, nutritionist_agent],
    termination_condition=termination,
)

# Example kickoff
user_input = "I'm looking for a quick, delicious dinner I can prep after work. I have 30 minutes and minimal clean-up is ideal."

In [ ]:
with langfuse.start_as_current_span(name="create_meal_plan") as span:
    async for message in team.run_stream(task=user_input):
        if isinstance(message, TaskResult):
            print("Stop Reason:", message.stop_reason)
        else:
            print(message)

    span.update_trace(
        input=user_input,
        output=message.stop_reason,
    )

# Flush the trace to Langfuse for short-lived environments such as Jupyter Notebooks
langfuse.flush()

### ట్రేస్ నిర్మాణం

Langfuse ఒక **ట్రేస్**ను రికార్డ్ చేస్తుంది, ఇది **స్పాన్లు** కలిగి ఉంటుంది, ఇవి మీ ఏజెంట్ లాజిక్ యొక్క ప్రతి దశను సూచిస్తాయి. ఇక్కడ, ట్రేస్ మొత్తం ఏజెంట్ రన్ మరియు ఉప-స్పాన్లను కలిగి ఉంది:
- మీల్ ప్లానర్ ఏజెంట్
- న్యూట్రిషనిస్ట్ ఏజెంట్లు

ఇవి పరిశీలించి, సమయం ఎక్కడ ఖర్చు అవుతుంది, ఎంత టోకెన్లు ఉపయోగించబడ్డాయి, మరియు ఇతర వివరాలను చూడవచ్చు:

![Langfuseలో ట్రేస్ చెట్టు](https://langfuse.com/images/cookbook/example-autogen-evaluation/trace-tree.png)

_[ట్రేస్‌కు లింక్](https://cloud.langfuse.com/project/cloramnkj0002jz088vzn1ja4/traces/dac2b33e7cd709e685ccf86a137ecc64)_


## ఆన్‌లైన్ మూల్యాంకనం

ఆన్‌లైన్ మూల్యాంకనం అంటే ఏజెంట్‌ను ప్రత్యక్ష, వాస్తవ ప్రపంచ పరిసరాల్లో, అంటే ఉత్పత్తిలో వాస్తవ వినియోగ సమయంలో పరీక్షించడం. ఇది వాస్తవ వినియోగదారుల పరస్పర చర్యలపై ఏజెంట్ పనితీరును పర్యవేక్షించడం మరియు ఫలితాలను నిరంతరం విశ్లేషించడం కలిగి ఉంటుంది.

### ఉత్పత్తిలో ట్రాక్ చేయవలసిన సాధారణ మెట్రిక్స్

1. **ఖర్చులు** — ఇన్‌స్ట్రుమెంటేషన్ టోకెన్ వినియోగాన్ని పట్టుకుంటుంది, దీన్ని టోకెన్‌కు ధర కేటాయించడం ద్వారా సుమారు ఖర్చులుగా మార్చవచ్చు.
2. **లేటెన్సీ** — ప్రతి దశను లేదా మొత్తం రన్‌ను పూర్తి చేయడానికి పట్టే సమయాన్ని గమనించండి.
3. **వినియోగదారుల అభిప్రాయం** — వినియోగదారులు ఏజెంట్‌ను మెరుగుపరచడానికి లేదా సరిదిద్దడానికి సహాయపడే ప్రత్యక్ష అభిప్రాయాన్ని (అంగీకారం/అంగీకారంలేని గుర్తులు) అందించగలరు.
4. **LLM-జడ్జ్‌గా** — మీ ఏజెంట్ అవుట్‌పుట్‌ను సమీప వాస్తవ సమయంలో (ఉదా: టాక్సిసిటీ లేదా సరైనతను తనిఖీ చేయడం) మూల్యాంకనం చేయడానికి వేరే LLMను ఉపయోగించండి.

క్రింద, ఈ మెట్రిక్స్ యొక్క ఉదాహరణలను చూపించాము.


#### 1. ఖర్చులు

క్రింద `gpt-4o-mini` కాల్స్ కోసం వినియోగాన్ని చూపించే స్క్రీన్‌షాట్ ఉంది. ఖర్చుతో కూడిన దశలను చూడటానికి మరియు మీ ఏజెంట్‌ను ఆప్టిమైజ్ చేయడానికి ఇది ఉపయోగకరంగా ఉంటుంది.

![ఖర్చులు](https://langfuse.com/images/cookbook/example-autogen-evaluation/gpt-4o-costs.png) 

_[ట్రేస్‌కు లింక్](https://cloud.langfuse.com/project/cloramnkj0002jz088vzn1ja4/traces/dac2b33e7cd709e685ccf86a137ecc64)_


#### 2. లేటెన్సీ

ప్రతి దశను పూర్తి చేయడానికి ఎంత సమయం పట్టిందో కూడా మనం చూడవచ్చు. క్రింది ఉదాహరణలో, మొత్తం ప్రాసెస్ పూర్తి కావడానికి సుమారు 3 సెకన్లు పట్టింది, దీన్ని దశలవారీగా విభజించవచ్చు. ఇది bottlenecks గుర్తించడంలో మరియు మీ ఏజెంట్‌ను ఆప్టిమైజ్ చేయడంలో సహాయపడుతుంది.

![లేటెన్సీ](https://langfuse.com/images/cookbook/example-autogen-evaluation/agent-latency.png) 

_[ట్రేస్‌కు లింక్](https://cloud.langfuse.com/project/cloramnkj0002jz088vzn1ja4/traces/dac2b33e7cd709e685ccf86a137ecc64?display=timeline)_


#### 3. వినియోగదారుల అభిప్రాయం

మీ ఏజెంట్ వినియోగదారు ఇంటర్‌ఫేస్‌లో అమర్చబడితే, మీరు నేరుగా వినియోగదారుల అభిప్రాయాన్ని (చాట్ UIలో థంబ్స్-అప్/డౌన్ వంటి) నమోదు చేయవచ్చు.


In [10]:
from langfuse import get_client
 
langfuse = get_client()
 
# Option 1: Use the yielded span object from the context manager
with langfuse.start_as_current_span(
    name="autogen-request-user-feedback-1") as span:
    
    async for message in team.run_stream(task="Create a meal with potatoes"):
            if isinstance(message, TaskResult):
                print("Stop Reason:", message.stop_reason)
            else:
                print(message)    
 
    # Score using the span object
    span.score_trace(
        name="user-feedback",
        value=1,
        data_type="NUMERIC",
        comment="This was delicious, thank you"
    )
 
# Option 2: Use langfuse.score_current_trace() if still in context
with langfuse.start_as_current_span(name="autogen-request-user-feedback-2") as span:
    # ... Autogen execution ...

    async for message in team.run_stream(task="I am allergic to gluten."):
            if isinstance(message, TaskResult):
                print("Stop Reason:", message.stop_reason)
            else:
                print(message)    
 
    # Score using current context
    langfuse.score_current_trace(
        name="user-feedback",
        value=1,
        data_type="NUMERIC"
    )

id='da068880-22ae-4f01-9f01-2bb231939089' source='user' models_usage=None metadata={} created_at=datetime.datetime(2025, 7, 2, 16, 20, 43, 732669, tzinfo=datetime.timezone.utc) content='Create a meal with potatoes' type='TextMessage'
id='ad937ce4-3534-493f-824b-ca9c226b5287' source='meal_planner_agent' models_usage=RequestUsage(prompt_tokens=95, completion_tokens=30) metadata={} created_at=datetime.datetime(2025, 7, 2, 16, 20, 45, 186423, tzinfo=datetime.timezone.utc) content='Potato and Spinach Frittata  \n- Eggs  \n- Potatoes  \n- Fresh spinach  \n- Onion  \n- Cheese (optional)  ' type='TextMessage'
id='50fd33c1-057f-49fe-afad-ee86d164296d' source='nutritionist_agent' models_usage=RequestUsage(prompt_tokens=132, completion_tokens=4) metadata={} created_at=datetime.datetime(2025, 7, 2, 16, 20, 45, 581059, tzinfo=datetime.timezone.utc) content='APPROVE' type='TextMessage'
Stop Reason: Text 'APPROVE' mentioned
id='e371de6c-e5fc-42c1-8eda-e5b8cd5accab' source='user' models_usage=None met

In [ ]:
# Option 3: Use create_score() with trace ID (when outside context)
langfuse.create_score(
    trace_id="predefined_trace_id",
    name="user-feedback",
    value=1,
    data_type="NUMERIC",
    comment="This was correct, thank you"
)

వినియోగదారుల అభిప్రాయం తరువాత Langfuse లో పొందుపరచబడుతుంది:

![వినియోగదారుల అభిప్రాయం Langfuse లో పొందుపరచబడుతుంది](https://langfuse.com/images/cookbook/example-autogen-evaluation/user-feedback.png)


#### 4. ఆటోమేటెడ్ LLM-as-a-Judge స్కోరింగ్

LLM-as-a-Judge అనేది మీ ఏజెంట్ అవుట్‌పుట్‌ను ఆటోమేటిక్‌గా అంచనా వేయడానికి మరో మార్గం. మీరు అవుట్‌పుట్ యొక్క సరైనత, విషపూరితత, శైలి లేదా మీకు అవసరమైన ఇతర ప్రమాణాలను అంచనా వేయడానికి ప్రత్యేక LLM కాల్‌ను సెట్ చేయవచ్చు.

**వర్క్‌ఫ్లో**:
1. మీరు ఒక **మూల్యాంకన టెంప్లేట్** నిర్వచిస్తారు, ఉదా., "టెక్స్ట్ విషపూరితమా అని తనిఖీ చేయండి."
2. మీరు జడ్జ్-మోడల్‌గా ఉపయోగించే మోడల్‌ను సెట్ చేస్తారు; ఈ సందర్భంలో `gpt-4o-mini` Azure ద్వారా ప్రశ్నించబడుతుంది.
3. ప్రతి సారి మీ ఏజెంట్ అవుట్‌పుట్‌ను ఉత్పత్తి చేసినప్పుడు, ఆ అవుట్‌పుట్‌ను టెంప్లేట్‌తో "జడ్జ్" LLMకి పంపిస్తారు.
4. జడ్జ్ LLM రేటింగ్ లేదా లేబుల్‌తో స్పందిస్తుంది, దాన్ని మీరు మీ ఆబ్జర్వబిలిటీ టూల్‌లో లాగ్ చేస్తారు.

Langfuse నుండి ఉదాహరణ:

![LLM-as-a-Judge Evaluator](https://langfuse.com/images/cookbook/example-autogen-evaluation/evaluator.png)


In [12]:
with langfuse.start_as_current_span(name="autogen-request-user-feedback-2") as span:

    async for message in team.run_stream(task="I am a picky eater and not sure if you find something for me."):
            if isinstance(message, TaskResult):
                print("Stop Reason:", message.stop_reason)
            else:
                print(message) 

    span.update_trace(
        input=user_input,
        output=message.stop_reason,
    )

langfuse.flush()

id='eefc628d-502f-451a-8f70-be486f62f8c5' source='user' models_usage=None metadata={} created_at=datetime.datetime(2025, 7, 2, 16, 38, 29, 171393, tzinfo=datetime.timezone.utc) content='I am a picky eater and not sure if you find something for me.' type='TextMessage'
id='13b3e14b-bcf7-42a5-80d6-54b0c7be765e' source='meal_planner_agent' models_usage=RequestUsage(prompt_tokens=352, completion_tokens=27) metadata={} created_at=datetime.datetime(2025, 7, 2, 16, 38, 30, 433516, tzinfo=datetime.timezone.utc) content='Chicken Alfredo Pasta  \n- Gluten-free pasta  \n- Grilled chicken breast  \n- Heavy cream  \n- Parmesan cheese  \n- Garlic  ' type='TextMessage'
id='550f2dee-0e08-4bbd-b67f-991b467328f1' source='nutritionist_agent' models_usage=RequestUsage(prompt_tokens=386, completion_tokens=17) metadata={} created_at=datetime.datetime(2025, 7, 2, 16, 38, 31, 505173, tzinfo=datetime.timezone.utc) content='Consider incorporating some vegetables, like spinach or broccoli, to increase the nutrien

మీరు ఈ ఉదాహరణ యొక్క సమాధానం "విషపూరితమైనది కాదు" అని నిర్ణయించబడిందని చూడవచ్చు.

![LLM-as-a-Judge మూల్యాంకన స్కోరు](https://langfuse.com/images/cookbook/example-autogen-evaluation/llm-as-a-judge-score.png)


#### 5. పరిశీలన మెట్రిక్స్ అవలోకనం

ఈ మెట్రిక్స్ అన్నీ డాష్‌బోర్డ్స్‌లో కలిపి చూడవచ్చు. ఇది మీ ఏజెంట్ అనేక సెషన్లలో ఎలా పనిచేస్తుందో త్వరగా చూడటానికి మరియు కాలక్రమంలో నాణ్యతా మెట్రిక్స్‌ను ట్రాక్ చేయడానికి సహాయపడుతుంది.

![పరిశీలన మెట్రిక్స్ అవలోకనం](https://langfuse.com/images/cookbook/example-autogen-evaluation/dashboard.png)


## ఆఫ్‌లైన్ మూల్యాంకనం

ఆన్‌లైన్ మూల్యాంకనం ప్రత్యక్ష అభిప్రాయానికి అవసరం, కానీ మీరు **ఆఫ్‌లైన్ మూల్యాంకనం** కూడా అవసరం—అంటే అభివృద్ధి ముందు లేదా అభివృద్ధి సమయంలో వ్యవస్థబద్ధమైన తనిఖీలు. ఇది మార్పులను ఉత్పత్తిలోకి తీసుకురాకముందు నాణ్యత మరియు నమ్మకాన్ని నిలుపుకోవడంలో సహాయపడుతుంది.


### డేటాసెట్ మదింపు

ఆఫ్లైన్ మదింపులో, మీరు సాధారణంగా:
1. ఒక బెంచ్‌మార్క్ డేటాసెట్ (ప్రాంప్ట్ మరియు ఆశించిన అవుట్‌పుట్ జంటలతో) కలిగి ఉంటారు  
2. ఆ డేటాసెట్‌పై మీ ఏజెంట్‌ను నడుపుతారు  
3. అవుట్‌పుట్‌లను ఆశించిన ఫలితాలతో పోల్చడం లేదా అదనపు స్కోరింగ్ మెకానిజాన్ని ఉపయోగించడం  

క్రింద, మేము ఈ విధానాన్ని [q&a-dataset](https://huggingface.co/datasets/junzhang1207/search-dataset) తో ప్రదర్శిస్తున్నాము, ఇది ప్రశ్నలు మరియు ఆశించిన సమాధానాలను కలిగి ఉంటుంది.


In [16]:
import pandas as pd
from datasets import load_dataset
 
# Fetch search-dataset from Hugging Face
dataset = load_dataset("junzhang1207/search-dataset", split = "train")
df = pd.DataFrame(dataset)
print("First few rows of search-dataset:")
print(df.head())

/Users/jannik/Documents/GitHub/ai-agents-for-beginners/.venv/lib/python3.13/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


First few rows of search-dataset:
                                     id  \
0  20caf138-0c81-4ef9-be60-fe919e0d68d4   
1  1f37d9fd-1bcc-4f79-b004-bc0e1e944033   
2  76173a7f-d645-4e3e-8e0d-cca139e00ebe   
3  5f5ef4ca-91fe-4610-a8a9-e15b12e3c803   
4  64dbed0d-d91b-4acd-9a9c-0a7aa83115ec   

                                            question  \
0                 steve jobs statue location budapst   
1  Why is the Battle of Stalingrad considered a t...   
2  In what year did 'The Birth of a Nation' surpa...   
3  How many Russian soldiers surrendered to AFU i...   
4   What event led to the creation of Google Images?   

                                     expected_answer       category       area  
0  The Steve Jobs statue is located in Budapest, ...           Arts  Knowledge  
1  The Battle of Stalingrad is considered a turni...   General News       News  
2  This question is based on a false premise. 'Th...  Entertainment       News  
3  About 300 Russian soldiers surrendered to t

తర్వాత, రన్స్‌ను ట్రాక్ చేయడానికి Langfuse లో డేటాసెట్ ఎంటిటీని సృష్టిస్తాము. ఆ తర్వాత, డేటాసెట్ నుండి ప్రతి అంశాన్ని సిస్టమ్‌లో చేర్చుతాము.


In [17]:
from langfuse import Langfuse
langfuse = Langfuse()
 
langfuse_dataset_name = "qa-dataset_autogen-agent"
 
# Create a dataset in Langfuse
langfuse.create_dataset(
    name=langfuse_dataset_name,
    description="q&a dataset uploaded from Hugging Face",
    metadata={
        "date": "2025-03-21",
        "type": "benchmark"
    }
)

Dataset(id='cmcm7524d00kjad07s2cjwqcf', name='qa-dataset_autogen-agent', description='q&a dataset uploaded from Hugging Face', metadata={'date': '2025-03-21', 'type': 'benchmark'}, project_id='cloramnkj0002jz088vzn1ja4', created_at=datetime.datetime(2025, 7, 2, 16, 54, 7, 357000, tzinfo=datetime.timezone.utc), updated_at=datetime.datetime(2025, 7, 2, 16, 54, 7, 357000, tzinfo=datetime.timezone.utc))

In [18]:
df_25 = df.sample(25) # For this example, we upload only 25 dataset questions

for idx, row in df_25.iterrows():
    langfuse.create_dataset_item(
        dataset_name=langfuse_dataset_name,
        input={"text": row["question"]},
        expected_output={"text": row["expected_answer"]}
    )

![Dataset items in Langfuse](https://langfuse.com/images/cookbook/example-autogen-evaluation/example-dataset.png)


#### డేటాసెట్‌పై ఏజెంట్‌ను నడపడం

మొదట, మేము ప్రశ్నలకు Azure OpenAI మోడల్స్ ఉపయోగించి సమాధానాలు ఇచ్చే ఒక సాధారణ Autogen ఏజెంట్‌ను రూపొందిస్తాము.


In [8]:
import os
from dotenv import load_dotenv

from autogen_agentchat.agents import AssistantAgent
from autogen_core.models import UserMessage
from autogen_ext.models.azure import AzureAIChatCompletionClient
from azure.core.credentials import AzureKeyCredential
from autogen_core import CancellationToken
from autogen_agentchat.messages import TextMessage

In [ ]:
load_dotenv()
client = AzureAIChatCompletionClient(
    model="gpt-4o",
    endpoint="https://models.inference.ai.azure.com",
    # To authenticate with the model you will need to generate a personal access token (PAT) in your GitHub settings.
    # Create your PAT token by following instructions here: https://docs.github.com/en/authentication/keeping-your-account-and-data-secure/managing-your-personal-access-tokens
    credential=AzureKeyCredential(os.getenv("GITHUB_TOKEN")),
    max_tokens=5000,
    model_info={
        "json_output": True,
        "function_calling": False,
        "vision": False,
        "family": "unknown",
        "structured_output": True,
    },
)

result = await client.create([UserMessage(content="What is the capital of France?", source="user")])
print(result)

In [18]:
agent = AssistantAgent(
    name="assistant",
    model_client=client,
    tools=[],
    system_message="You are participant in a quizz show and you are given a question. You need to create a short answer to the question.",
)

అప్పుడు, మేము సహాయక ఫంక్షన్ `my_agent()` ను నిర్వచిస్తాము.


In [19]:
async def my_agent(user_query: str):

    with langfuse.start_as_current_span(name="autogen-trace") as span:

        # Execute the agent response
        response = await agent.on_messages(
            [TextMessage(content=user_query, source="user")],
            cancellation_token=CancellationToken(),
        )

        span.update_trace(
            input=user_query,
            output=response.chat_message.content,
        )

    return str(response.chat_message.content)

# Test the function
await my_agent("What is the capital of France?")

'The capital of France is Paris.'

చివరగా, ప్రతి డేటాసెట్ అంశాన్ని లూప్ చేసి, ఏజెంట్‌ను నడిపించి, ట్రేస్‌ను డేటాసెట్ అంశానికి లింక్ చేస్తాము. అవసరమైతే, ఒక వేగవంతమైన మూల్యాంకన స్కోర్‌ను కూడా జతచేయవచ్చు.


In [20]:
dataset_name = "qa-dataset_autogen-agent"
current_run_name = "dev_tasks_run-autogen_gpt-4.1" # Identifies this specific evaluation run
current_run_metadata={"model_provider": "Azure", "model": "gpt-4.1"}
current_run_description="Evaluation run for Autogen model on July 3rd"

dataset = langfuse.get_dataset('qa-dataset_autogen-agent')

for item in dataset.items:
    print(f"Running evaluation for item: {item.id} (Input: {item.input})")
 
    # Use the item.run() context manager
    with item.run(
        run_name=current_run_name,
        run_metadata=current_run_metadata,
        run_description=current_run_description
    ) as root_span: 
        # All subsequent langfuse operations within this block are part of this trace.
        generated_answer = await my_agent(user_query = item.input["text"])
    
    print("Generated Answer: ", generated_answer)
 
print(f"\nFinished processing dataset '{dataset_name}' for run '{current_run_name}'.")

langfuse.flush()

Running evaluation for item: 09810cc4-9992-4712-a3b2-7224da31776a (Input: {'text': 'In Hindu mythology, which deity is the Ganges river dolphin associated with?'})
Generated Answer:  In Hindu mythology, the Ganges river dolphin is associated with the deity Ganga.
Running evaluation for item: bb113f94-7723-47c6-8c34-59d883044514 (Input: {'text': 'What significant discovery did the LHCb collaboration report in 2015?'})
Generated Answer:  In 2015, the LHCb collaboration reported the discovery of pentaquark particles.
Running evaluation for item: 4d8ae54e-ceab-46d0-ad2c-6e8e223589a9 (Input: {'text': 'What is the MÄ\x81ori name for the red-crowned parakeet?'})
Generated Answer:  The Māori name for the red-crowned parakeet is kākāriki.
Running evaluation for item: 21e5a0d5-f619-4a73-868e-9955053b3e72 (Input: {'text': 'Who starred in the 1978 television film adaptation of Les MisÃ©rables?'})
Generated Answer:  Richard Jordan starred as Jean Valjean in the 1978 television film adaptation of Le

మీరు ఈ ప్రక్రియను వివిధ ఏజెంట్ కాన్ఫిగరేషన్లతో పునరావృతం చేయవచ్చు, ఉదాహరణకు:
- మోడల్స్ (gpt-4o-mini, gpt-4.1, మొదలైనవి)
- ప్రాంప్ట్స్
- టూల్స్ (సెర్చ్ వర్సెస్ సెర్చ్ లేకుండా)
- ఏజెంట్ సంక్లిష్టత (బహుళ ఏజెంట్ వర్సెస్ సింగిల్ ఏజెంట్)

తర్వాత వాటిని Langfuse లో పక్కపక్కన పోల్చండి. ఈ ఉదాహరణలో, నేను 25 డేటాసెట్ ప్రశ్నలపై ఏజెంట్‌ను 3 సార్లు నడిపాను. ప్రతి రన్ కోసం, నేను వేర్వేరు Azure OpenAI మోడల్‌ను ఉపయోగించాను. మీరు పెద్ద మోడల్‌ను ఉపయోగించినప్పుడు సరైన సమాధానాల సంఖ్య మెరుగుపడుతుందని చూడవచ్చు (అనుకున్నట్లుగా). `correct_answer` స్కోర్ [LLM-as-a-Judge Evaluator](https://langfuse.com/docs/scores/model-based-evals) ద్వారా రూపొందించబడింది, ఇది డేటాసెట్‌లో ఇచ్చిన నమూనా సమాధానంపై ఆధారపడి ప్రశ్న సరైనదా అని తీర్పు ఇవ్వడానికి సెటప్ చేయబడింది.

![డేటాసెట్ రన్ అవలోకనం](https://langfuse.com/images/cookbook/example-autogen-evaluation/dataset_runs.png)
![డేటాసెట్ రన్ పోలిక](https://langfuse.com/images/cookbook/example-autogen-evaluation/dataset-run-comparison.png)


---

<!-- CO-OP TRANSLATOR DISCLAIMER START -->
**విమర్శ**:  
ఈ పత్రాన్ని AI అనువాద సేవ [Co-op Translator](https://github.com/Azure/co-op-translator) ఉపయోగించి అనువదించారు. మేము ఖచ్చితత్వానికి ప్రయత్నిస్తున్నప్పటికీ, ఆటోమేటెడ్ అనువాదాలలో తప్పులు లేదా అసమానతలు ఉండవచ్చు. దాని స్వదేశీ భాషలోని అసలు పత్రాన్ని అధికారం కలిగిన మూలంగా పరిగణించాలి. కీలకమైన సమాచారం కోసం, ప్రొఫెషనల్ మానవ అనువాదాన్ని సిఫారసు చేస్తాము. ఈ అనువాదాన్ని ఉపయోగించడం వల్ల కలిగే ఏవైనా అపార్థాలు లేదా తప్పుదారులు కోసం మేము బాధ్యత వహించము.
<!-- CO-OP TRANSLATOR DISCLAIMER END -->
